# Практическая работа №4. Автоматическая оптимизация нейронной сети с помощью Apache TVM

## 1. Цели и задачи работы

**Цель работы** – изучить программный интерфейс для автоматической оптимизации нейронных сетей
с помощью Apache TVM на процессорах архитектуры RISC-V.

Достижение указанной цели предполагает решение следующих **задач**:

1. Обучение архитектур логистической регрессии и полносвязной нейронной сети
   на наборе данных MNIST на x86-устройстве. Сохранение модели в формате Apache TVM,
   а также сохранение метрик качества и набора данных в формате NumPy для дальнейшего
   тестирования.
1. Установка LLVM и сборка Apache TVM с LLVM.
1. Оптимизация модели логистической регрессии.
   1. Загрузка модели логистической регрессии. Запуск, проверка корректности и измерение
      времени инференса без оптимизации.
   1. Оптимизация модели логистической регрессии с помощью AutoTVM, Auto-scheduler,
      MetaScheduler.
   1. Анализ результатов оптимизации логистической регрессии.
1. Оптимизация полносвязной нейронной сети.
   1. Загрузка модели полносвязной нейронной сети. Запуск, проверка корректности и измерение
      времени инференса без оптимизации.
   1. Оптимизация модели полносвязной нейронной сети с помощью AutoTVM,
      Auto-scheduler, MetaScheduler.
   1. Анализ результатов оптимизации полносвязной нейронной сети.

Полезные ссылки:
- [AutoTVM туториалы](https://tvm.apache.org/docs/how_to/tune_with_autotvm/index.html),
- [AutoTVM документация](https://tvm.apache.org/docs/reference/api/python/autotvm.html),
- [Auto-scheduler туториалы](https://tvm.apache.org/docs/how_to/tune_with_autoscheduler),
- [Auto-scheduler документация](https://tvm.apache.org/docs/reference/api/python/auto_scheduler.html),
- [MetaScheduler документация](https://tvm.apache.org/docs/reference/api/python/meta_schedule.html).

## 2. Обучение моделей глубокого обучения

Обучение моделей выполняется на архитектуре x86 с использованием библиотеки PyTorch, так как
на момент подготовки материалов работы отсутствует официальная сборка PyTorch для RISC-V-устройств.

### 2.1 Установка зависимостей для обучения моделей

#### 2.1.2 Установка Apache TVM  

Вначале необходимо установить Apache TVM той же версии, что будет использоваться на устройстве
RISC-V, для совместимости формата хранения графа вычислений. Для этого необходимо установить
LLVM и собрать Apache TVM из исходных кодов по аналогии с тем, как это было сделано в предыдущей
практической работе. Ниже приведена соответствующая последовательность команд.

```bash
sudo apt install clang-17 llvm-17*
```

```bash
git clone --recursive https://github.com/apache/tvm
cd tvm

mkdir build
cd build

cmake -DUSE_LLVM=ON ..
make
```


#### 2.1.2 Настройка окружения Python 

Далее будем считать, что на x86-узле установлена Miniconda. Соответственно создадим виртуальное
окружение для подготовки тестовых моделей. Для обучения моделей используется библиотека PyTorch
и набор данных MNIST. Поэтому потребуется пакет `torch`, обеспечивающий функционал, необходимый
для обучения/тестирования нейронных сетей, и `torchvision`, содержащий вспомогательные функции,
в частности, для загрузки широко известных наборов данных. Далее приведена примерная
последовательность команд для создания и настройки окружения.

```bash
conda create -n torch_train python==3.10
conda activate torch_train

pip install numpy matplotlib torchmetricspip3 install torch torchvision --index-url https://download.pytorch.org/whl/cu118
pip install notebook 
```


## 2.2 Обучение моделей

Перед обучением модели необходимо активировать созданное на предыдущем этапе виртуальное
окружение и установить путь к Apache TVM.

```bash
conda activate torch_train
export PYTHONPATH=<PATH TO TVM>/python:${PYTHONPATH}
```

Процесс обучения реализован в файле ```04_train_model_x86.ipynb```. Более подробно
возможности библиотеки PyTorch для обучения моделей рассматривались во второй практической
работе. Необходимо запустить выполнение этого файла. После завершения его работы архитектура
и веса обученных нейронных сетей будут сохранены в файл в директории ```model/```. В этой же
директории будет сохранен файл с показателями точности моделей. Наряду с этим, указанный скрипт
обеспечивает сохранение тестовых данных (изображения и их метки) для упрощения процедуры
их загрузки на RISC-V-устройствах. Соответственное данные сохраняются в директорию ```data/```.

## 3. Сборка и установка LLVM и Apache TVM


### 3.1. Сборка LLVM

В данной практической работе не используется кросс-компиляция моделей или слоев. Компиляция происходит
на устройстве с архитектурой RISC-V. Поэтому требуется собрать Apache TVM с LLVM. Рекомендуется
использовать версию 15 <= LLVM <= 17.

#### 3.1.1. Установка с помощью менеджера пакетов

```bash
sudo apt install clang-17 llvm-17*
```

#### 3.1.1. Сборка LLVM версии llvmorg-17.0.6 (для версии llvmorg-17.0.6)

Для сборка LLVM из исходных кодов требуется загрузить необходимую версию LLVM из репозитори
 GitHub. В данном работе используется версия llvmorg-17.0.6, далее, используя утилиту CMake
 сгенерировать make-файлы и выполнить сборку. Ниже приведена соответствующая последовательност
 команд.

```bash
git clone https://github.com/llvm/llvm-project.git -b llvmorg-17.0.6
cd llvm-project

mkdir _build
cd _build

cmake -DCMAKE_BUILD_TYPE="Release" \
      -DLLVM_ENABLE_PROJECTS=clang \
      -DBUILD_SHARED_LIBS=True \
      -DLLVM_USE_SPLIT_DWARF=True \
      -DCMAKE_INSTALL_PREFIX="../../_install" ../llvm

make
```
**Примечание:** в случае сборки LLVM из исходных кодов перед сборкой Apache TVM необходимо
указать путь к LLVM в переменной окружения `PATH` и создать переменную окружения `LLVM_CONFIG`.
Ниже показан пример. 

```bash
PATH="<PATH TO LLVM>/_build/bin:$PATH"
export LLVM_CONFIG=<PATH TO LLVM>/_build/bin/llvm-config
```

### 3.2. Установка OpenBLAS
Далее необходимо установить OpenBLAS, используя менеджер пакетов.

```bash
sudo apt-get install libopenblas-dev
```

### 3.3. Настройка окружения Python
Для выполнения практической работы создадим и настроим виртуальное окружение Python так,
как показано ниже:

```bash
python3 -m venv ~/tvm_cpu/
source ~/tvm_cpu/bin/activate

pip install scipy numpy matplotlib pandas
pip install cloudpickle traitlets typing-extensions psutil pybind11 decorator attrs 
pip install notebook 

```

### 3.4. Сборка Apache TVM
Для сборки Apache TVM используем ветку main GitHub-репозитория, так как недавно были внесены
критически важные исправленияя [1](https://discuss.tvm.apache.org/t/run-tvm-software-stack-on-risc-v/17683/10)
и [2](https://github.com/apache/tvm/pull/17347). Для сборки Apache TVM не обязательн
 использовать созданную виртуальную среду для Python.

```bash
git clone --recursive https://github.com/apache/tvm
cd tvm

mkdir build
cd build

cmake -DUSE_LLVM=ON -DUSE_BLAS=openblas ..
make
```

### 3.5. Активация окружения для практической работы 
Для активации виртуальной среды с целью решения задач практической работы необходимо
выполнить следующие команды:

```bash
source ~/tvm_cpu/bin/activate
export PYTHONPATH=<PATH TO TVM>/python:${PYTHONPATH}
```

## 4. Программная реализация вспомогательных функций

### 4.1. Импорт пакетов

Для использования функционала Apache TVM и других вспомогательных библиотек импортируем
необходимые пакеты.

Также определим переменную, содержащую используемый тип данных для элементов тензоров -
`float32`, а также установим в качестве целевого устройства для запуска `CPU`.

In [ ]:
import os
from time import time

import matplotlib.pyplot as plt


import numpy as np
import tvm

from tvm import autotvm
from tvm import auto_scheduler
from tvm import meta_schedule as ms

from tvm import relay
from tvm.autotvm.tuner import XGBTuner
from tvm.contrib import graph_executor


dtype = 'float32'
dev = tvm.cpu()

global_trial = 96

### 4.2. Строка компиляции

На данном этапе определим строку компиляции ```target```. Компиляция нейронных сетей
происходит на устройстве с архитектурой RISC-V без использования кросс-компиляции.
Для упрощения тестирования и отладки добавлена возможность запуска на ```x86_64```.

### 4.3. Уровень оптимизации графа

При запусках на устройствах RISC-V используется ```opt_level=2```, в случае запуска на архитектуре
x86-64 используется ```opt_level=3```.

In [ ]:
def is_x86():
    if tvm.target.Target('llvm').attrs.get('mtriple') is None:
        return True
    return 'x86_64' in tvm.target.Target('llvm').attrs.get('mtriple')

def is_riscv():
    return 'riscv64' in tvm.target.Target('llvm').attrs.get('mtriple')
    

print(f"mtriple устройства {tvm.target.Target('llvm').attrs.get('mtriple')}")

if is_x86():
    target = tvm.target.Target('llvm')
    opt_level = 3
elif is_riscv():
    target = tvm.target.Target(
        'llvm -jit=orcjit -mtriple=riscv64-unknown-linux-gnu '
        '-mcpu=generic-rv64 -mabi=lp64d -mattr=+64bit,+m,+a,+f,+d'
    )
    opt_level = 2
else:
    raise ValueError("Unsupported architecture")

print(f'{target = }')

### 4.3 Вспомогательные функции

Реализуем функцию ```load_model``` для загрузки модели в формате TVM, а также функцию
```load_images_and_labels``` для загрузки изображений и меток из набора данных MNIST.

In [ ]:
def load_model(mod_file, params_file):
    with open(mod_file, "r") as fo:
        mod = fo.read()
        
    mod = tvm.ir.load_json(mod)

    with open(params_file, "rb") as fo:
        params = relay.load_param_dict(fo.read())
    
    return mod, params

def load_images_and_labels(images_path, labels_path):
    images = np.load(images_path)
    labels = np.load(labels_path)
    
    return images, labels

Далее выполним реализацию функции `timeit_inference` для измерения времени инференса
и функции `get_accuracy` для определения качества решения задачи. 

1. Функция `timeit_inference`. Измерение времени инференса проводится на наборе данных MNIST.
   Инференс выполняется отдельно для каждого изображения из набора данных MNIST. Время выполнения
   и результаты предсказания (номер класса, на котором достигается максимумальная достоверность)
   возвращаются из функции.
1. Функция `get_accuracy`. Определение качества решения задачи выполняется для всего набора
   данных MNIST посредством сравнения результатов предсказания и разметки. Точность вычисляется
   как отношение количества совпадений предсказанных и размеченных классов к общему числу изображений
   в наборе данных.

In [ ]:
def timeit_inference(mod, lib, images):
    input_name = mod['main'].params[0].name_hint
    input_shape = mod['main'].params[0].type_annotation.shape
    input_shape = [int(s) for s in input_shape]

    dev = tvm.cpu()
    module = graph_executor.GraphModule(lib["default"](dev))
    
    predict = []
    times = []
    for i in range(len(images)):
        img = np.array(images[i:i+1], dtype=np.float32).reshape(input_shape)
        module.set_input(input_name, img)

        ts = time()
        module.run()
        tf = time()
        times.append((tf - ts) * 1000)
        
        output = module.get_output(0).numpy()
        predict.append(np.argmax(output))
        
    return np.array(predict), np.array(times)
    
def get_accuracy(labels, predict):
    return np.mean(labels == predict)

На данном этапе необходимо загрузить изображения, разметку и информацию о точности работы
нейронных сетей, полученную после обучения на системе с архитектурой x86-64.
Далее при решении задач практической работы точность нейронной сети необходимо сопоставлять
с загруженными значениями.

In [ ]:
images, labels = load_images_and_labels('data/test_images.npy', 'data/test_labels.npy')

metric = np.load('model/metric.npy', allow_pickle='TRUE').item()
print(metric)

## 5. Общая информация про методы автоматической оптимизации слоев в Apache TVM

Интерфейс методов автоматической оптимизации в Apache TVM имеет схожие элементы.
Сначала происходит извлечение задач, где задачей считается слой или подграф нейронной сети.
После этого каждая задача подвергается оптимизации. Результаты оптимизации логируются
либо в файл, либо в отдельную директорию.

Ключевым параметром в процессе оптимизации является количество итераций оптимизации задач.
Подбор этого параметра является нетривиальной задачей:

- Если значение параметра слишком маленькое, эффективное решение может не быть найдено.
- Слишком большое значение параметра приведет к значительным затратам времени.
- Оптимальное количество итераций зависит от характеристик нейронной сети, целевого устройства
  и используемого метода оптимизации.

На каждой итерации выполняется несколько проверок качества конкретной реализации.
Параметры этих проверок задаются через обьекты классов [```autotvm.measure_option```](https://tvm.apache.org/docs/reference/api/python/autotvm.html#tvm.autotvm.measure.measure_option),
[```auto_scheduler.LocalRunner```](https://tvm.apache.org/docs/reference/api/python/auto_scheduler.html#tvm.auto_scheduler.LocalRunner)
и ```ms.runner.LocalRunner```, которые предоставляют интерфейс для указания числа замеров
производительности:

- ```number``` - количество запусков кода для усреднения времени выполнения в процессе одного замера.
- ```repeat``` - число замеров. Всего выполняется (1 + number x repeat) запусков,
  где первый запуск используется для прогрева и не учитывается.
- ```enable_cpu_cache_flush``` очищает кэш CPU между последовательными замерами для более точной оценки
  задержек.

Таким образом, чем больше значение ```number x repeat```, тем более точной будет оценка времени
работы планов вычислений, однако, это также увеличивает продолжительность процесса автоматической
оптимизации.

**Примечание**: псевдокод работы методов оценки времени выполнения в Apache TVM приведен ниже.

```python
for r in range(repeat):
    time_start = now()
    for n in range(number):
        func_name()
    time_end = now()
    total_times.append((time_end - time_start) / number)
```

## 6. Запуск и оптимизация модели логистической регрессии 

### 6.1. Компиляция и запуск модели

Вначале необходимо выполнить загрузку модели логистической регрессии.

In [ ]:
default_logreg_time, autotvm_logreg_time, autoscheduler_logreg_time, ms_logreg_time = 0, 0, 0, 0

mod, params = load_model('model/logreg.json', 'model/logreg.params')
print(mod['main'])

Следующий шаг - компиляция модели без оптимизации слоев.

In [ ]:
with tvm.transform.PassContext(opt_level=opt_level):
    lib = relay.build(mod, target=target, params=params)

После компиляции можно выполнить запуск вывода и измерение времени выполнения с использованием
разработанной функции `timeit_inference`, а также определение качества работы логистической регрессии
с помощью функции `get_accuracy` и сравнение полученной точности классификации с загруженным
значением, которое получено на x86-64.

In [ ]:
default_logreg_predict, default_logreg_times = timeit_inference(mod, lib, images)

default_logreg_accuracy = get_accuracy(labels, default_logreg_predict)
assert np.allclose(metric['logreg'], default_logreg_accuracy, rtol=1e-5)

default_logreg_time = np.median(default_logreg_times)
print(f'Медианное время работы неоптимизированной модели: {default_logreg_time:.4f} мc')

### 6.2. Использованием возможностей AutoTVM

Определим функцию ```get_autotvm_task``` для извлечения задач и вывода информации
о задачах (номер задачи и ```task.workload```). Для этого используем метод
```autotvm.task.extract_from_program```, передав на вход модель, целевое устройство
и обученные параметры модели. В данном случае рассматриваются два типа задач:
полносвязные слои без трансформации весов и с трансформацией весов для улучшения
работы с памятью.

Для архитектур x86 и RISC-V задачи обозначаются как ```dense_*.x86```. На данный момент
в Apache TVM нет реализаций планов вычислений для RISC-V. Благодаря тому, что Apache TVM
опирается на возможности LLVM в процессе компиляции и сходство архитектур, инструмент
успешно использует планы вычислений, разработанные для x86-платформ, на устройствах
с архитектурой RISC-V.

In [ ]:
def get_autotvm_task(
    mod: tvm.ir.module.IRModule, 
    target: tvm.target.target.Target, 
    params: tvm.ir.container.Map
) -> list[tvm.autotvm.task.task.Task, ...]:
    """
    Параметры:
        mod: Модуль IRModule.
        target: Строка компиляции.
        params: Веса нейронной сети.
    
    Возвращаемое значение:
        Список задач.
    """

    # <РЕАЛИЗАЦИЯ ИЗВЛЕЧЕНИЯ ЗАДАЧ ИЗ ГРАФА ВЫЧИСЛЕНИЙ С ПОМОЩЬЮ AUTOTVM>

    return 

Вызовем разработанную функцию ```get_autotvm_task``` для извлечения задач
из графа вычислений для AutoTVM.

In [ ]:
tasks = get_autotvm_task(mod, target, params)

Следующий этап после извлечения задач - это оптимизация каждой задачи. Для этого
необходимо реализовать функцию ```tune_autotvm```, содержащую установку параметров
оптимизации и ее запуск.

Вначале необходимо определить параметры проверки времени выполнения каждого плана
с помощью [```autotvm.measure_option```](https://tvm.apache.org/docs/reference/api/python/autotvm.html#tvm.autotvm.measure.measure_option)
и [```autotvm.LocalRunner```](https://tvm.apache.org/docs/reference/api/python/autotvm.html#tvm.autotvm.measure.measure_methods.LocalRunner).
Затем для каждой задачи определить модель затрат. В качестве модели затрат для оценки
времени выполнения слоя используется метод градиентного бустинга деревьев, реализованный
на базе XGBoost. Apache TVM предоставляет интерфейс для нескольких [методов оптимизации](https://tvm.apache.org/docs/reference/api/python/autotvm.html#module-tvm.autotvm.tuner).
Инициализируем для каждой задачи класс
[```XGBTuner```](https://tvm.apache.org/docs/reference/api/python/autotvm.html#module-tvm.autotvm.tuner]).

Каждая задача оптимизируется ```min(n_trial, len(task.config_space))``` раз, где ```n_trial``` -
заданное количество попыток, а ```len(task.config_space)``` - количество различных
конфигураций в плане вычислений для данного тензорного выражения.

После определения всех параметров необходимо запустить оптимизацию с помощью метода
[```tuner_obj.tune```](https://tvm.apache.org/docs/reference/api/python/autotvm.html#tvm.autotvm.tuner.XGBTuner.tune),
передав в качестве параметров количество экспериментов оптимизации для каждой задачи, объект ```measure_option```
и название файла для логирования через ```autotvm.callback.log_to_file(log_file)```.

In [ ]:
def tune_autotvm(
    tasks: list[tvm.autotvm.task.task.Task, ...], 
    n_trial: int, 
    log_file: str
):
    """
    Параметры:
        tasks: Список задач.
        n_trial: Количество экспериментов для каждой задачи.
        log_file: Файл для логирование результатов оптимизации.
    """    

    # <ОПТИМИЗАЦИЯ СЛОЕВ С ПОМОЩЬЮ AUTOTVM>
    

Для запуска оптимизации с помощью AutoTVM необходимо определить файл ```log_file```
для логирование результатов оптимизации, установить число экспериментов при оптимизации,
а затем вызвать разработанную функцию ```tune_autotvm```.

In [ ]:
os.makedirs('autotvm/', exist_ok=True)
log_file = 'autotvm/autotvm_logreg.log'
n_trial = global_trial

tune_autotvm(tasks, n_trial, log_file)

Перед использованием оптимизированной модели необходимо выполнить компиляцию модели
с учетом истории оптимизации, которая была сохранена в файл `log_file`.

In [ ]:
with autotvm.apply_history_best(log_file):
    with tvm.transform.PassContext(opt_level=opt_level):
        lib = relay.build(mod, target=target, params=params)

На данном этапе можно выполнить измерение времени вывода с использованием функции
`timeit_inference`, проверку качества работы оптимизированной модели с помощью функции
`get_accuracy` и сравнение точности классификации с рефенсным значением, которое было
получено после запуска обучения модели.

In [ ]:
autotvm_logreg_predict, autotvm_logreg_times = timeit_inference(mod, lib, images)

autotvm_logreg_accuracy = get_accuracy(labels, autotvm_logreg_predict)
assert np.allclose(metric['logreg'], autotvm_logreg_accuracy, rtol=1e-5)

autotvm_logreg_time = np.median(autotvm_logreg_times)
print(f'Медианное время работы после оптимизации слоев с помощью AutoTVM: {autotvm_logreg_time:.4f} мc')

### 6.3. Использование Auto-scheduler

Определим функцию ```get_auto_scheduler_task``` для извлечения задач и вывода
информации о задачах (номер задачи и ```task.desc```).

Аналогично AutoTVM, вначале необходимо извлечь задачи, используя метод 
[```auto_scheduler.extract_tasks```](https://tvm.apache.org/docs/reference/api/python/auto_scheduler.html?highlight=extract_tasks#tvm.auto_scheduler.extract_tasks), передав в качестве входных параметров
модель, целевое устройство для запуска вывода, набор обученных параметров модели. Также Auto-scheduler
позволяет регулировать уровень оптимизации графа с помощью параметра ```opt_level```. Это значение
должно совпадать с уровнем оптимизации графа вычислений при компиляции модели. Отметим, что
в данном случае, граф вычислений состоит только из одного слоя, поэтому объединение слоев
не будет выполняться. Метод возвращает значение ```task_weights```, которое определяет вес
каждого подграфа. По умолчанию вес равен $1$. Если присутствуют $N$ одинаковых подграфов, то они
будут представлены в виде одной задачи с весом $N$.

In [ ]:
def get_auto_scheduler_task(
    mod: tvm.ir.module.IRModule, 
    target: tvm.target.target.Target, 
    params: tvm.ir.container.Map,
    opt_level: int
) -> tuple[list[tvm.auto_scheduler.search_task.SearchTask, ...], list[int, ...]]:
    """
    Параметры:
        mod: Модуль IRModule.
        target: Строка компиляции.
        params: Веса нейронной сети.
        opt_level: Уровень оптимизации графа вычислений.
    
    Возвращаемое значение:
        Список задач и список весов задач.
    """

    # <РЕАЛИЗАЦИЯ ИЗВЛЕЧЕНИЯ ЗАДАЧ И ВЕСОВ ЗАДАЧ ИЗ ГРАФА ВЫЧИСЛЕНИЙ С ПОМОЩЬЮ AUTO-SCHEDULER>
    
    return 

Выполним извлечение задач для Auto-scheduler, вызвав функцию ```get_auto_scheduler_task```.

In [ ]:
tasks, task_weights = get_auto_scheduler_task(mod, target, params, opt_level)

Далее реализуем функцию ```tune_auto_scheduler``` для автоматической настройки параметров
оптимизации нейронной сети.

В данном случае для оптимизации необходимо создать обьект класса
[```auto_scheduler.TaskScheduler```](https://tvm.apache.org/docs/reference/api/python/auto_scheduler.html?highlight=taskscheduler#tvm.auto_scheduler.TaskScheduler) с описанием задач
и определить параметры оптимизации [```auto_scheduler.TuningOptions```](https://tvm.apache.org/docs/reference/api/python/auto_scheduler.html?highlight=tuningoptions#tvm.auto_scheduler.TuningOptions). После этого можно вызвать метод
`tune` для созданного объекта класса `auto_scheduler.TaskScheduler`.

**Примечания:**

1. При определении параметров оптимизации используется параметр
   ```num_measures_per_round```. Он определяет количество конфигураций аннотированных эскизов,
   для которых будет измерено время перед обновлением базы результатов. После обновления
   базы результатов модель затрат переобучается, и запускается новая итерация
   эволюционного алгоритма для генерации новых эскизов.
1. Параметр количества оптимизаций ```num_measure_trials``` в Auto-scheduler задает общее
   количество измерений для всех подграфов.

In [ ]:
def tune_auto_scheduler(
    tasks: list[tvm.auto_scheduler.search_task.SearchTask, ...], 
    task_weights: list[int, ...], 
    log_file: str, 
    n_trials: int
):
    """
    Параметры:
        tasks: Список задач.
        task_weights: Список весов задач.
        n_trial: Количество экспериментов для каждой задачи.
        log_file: Файл для логирования результатов оптимизации.
    """
    
    # <ОПТИМИЗАЦИЯ ПОДГРАФОВ С ПОМОЩЬЮ AUTO-SCHEDULER>


На данном этапе можно выполнить запуск оптимизации с помощью Auto-scheduler.
Определим файл с навзанием ```log_file``` для логирования результатов оптимизации.
Установим число экспериментов при оптимизации равным ```N * len(tasks)```. Выполним
запуск оптимизации посредством вызова  функции ```tune_auto_scheduler```.

In [ ]:
os.makedirs('auto_schedule/', exist_ok=True)
log_file = 'auto_schedule/auto-schedule_logreg.log'
n_trial_per_task = global_trial

tune_auto_scheduler(tasks, task_weights, log_file, n_trial_per_task * len(tasks))

По завершении оптимизации необходимо скомпилировать модель с учетом истории оптимизации.

In [ ]:
with auto_scheduler.ApplyHistoryBest(log_file):
    with tvm.transform.PassContext(
        opt_level=opt_level, config={"relay.backend.use_auto_scheduler": True},
    ):
        lib = relay.build(mod, target=target, params=params)

Далее для скомпилированной модели можно выполнить измерение времени выполнения
с использованием вызова функции `timeit_inference`, определить качество работы
с помощью функции `get_accuracy` и проверить корректность, сравнив полученное
значение показателя точности с референсным значением.

In [ ]:
autoscheduler_logreg_predict, autoscheduler_logreg_times = timeit_inference(mod, lib, images)

autoscheduler_logreg_accuracy = get_accuracy(labels, autoscheduler_logreg_predict)
assert np.allclose(metric['logreg'], autoscheduler_logreg_accuracy, rtol=1e-5)

autoscheduler_logreg_time = np.median(autoscheduler_logreg_times)
print(f'Медианное время работы после оптимизации слоев с помощью Auto-scheduler: {autoscheduler_logreg_time:.4f} мc')

### 6.4. Применение MetaScheduler

Использование MetaScheduler требует указания числа ядер при формировании строки,
содержащей параметры целевого устройства, например, ```-num-cores 4```. Данный
параметр можно указать равным количеству физических ядер на устройстве. Внесем
соответствующие изменения в исходный код.

In [ ]:
print(f"mtriple устройства {tvm.target.Target('llvm').attrs.get('mtriple')}")

if is_x86():
      target = tvm.target.Target('llvm -num-cores 6')
elif is_riscv():    
    target = tvm.target.Target(
        'llvm -jit=orcjit -mtriple=riscv64-unknown-linux-gnu '
        '-mcpu=generic-rv64 -mabi=lp64d -mattr=+64bit,+m,+a,+f,+d -num-cores 4'
    )
else:
    raise ValueError("Unsupported architecture")


    print(f'{target = }')

Определим функцию ```get_ms_task``` для извлечения задач и вывода информации
о задачах (номер задачи и ```task.task_name```). Аналогично предыдущим методам
оптимизации, извлечение задач выполняется с помощью методов ```ms.relay_integration.extract_tasks```
и ```ms.relay_integration.extracted_tasks_to_tune_contexts```.

In [ ]:
def get_ms_task(
    mod: tvm.ir.module.IRModule, 
    target: tvm.target.target.Target, 
    params: tvm.ir.container.Map,
    opt_level: int,
    work_dir: str
) -> tuple[list[tvm.meta_schedule.tune_context.TuneContext, ...], list[int, ...]]:
    """
    Параметры:
        mod: Модуль IRModule.
        target: Строка компиляции.
        params: Веса нейронной сети.
        opt_level: Уровень оптимизации графа вычислений.
        work_dir: Директория для логирования результатов оптимизации.
    
    Возвращаемое значение:
        Список задач и список весов задач.
    """

    # <РЕАЛИЗАЦИЯ ИЗВЛЕЧЕНИЯ ЗАДАЧ И ВЕСОВ ЗАДАЧ ИЗ ГРАФА ВЫЧИСЛЕНИЙ С ПОМОЩЬЮ METASCHEDULER>
    
    return 

Вызовем разработанную функцию ```get_ms_task```, предварительно определив
директорию ```work_dir``` для логирования результатов оптимизации.

In [ ]:
work_dir = "meta_schedule_logreg"

if is_x86():
    tasks, task_weights = get_ms_task(mod, target, params, opt_level, work_dir)

По аналогии с другими рассмотренными методами реализуем функцию ```tune_ms```
для автоматической настройки параметров запуска вывода нейронной сети. Данная функция 
должна вызывать метод [```ms.tune.tune_tasks```](https://tvm.apache.org/docs/reference/api/python/meta_schedule.html?highlight=tune_tasks#tvm.meta_schedule.tune_tasks), который принимает на вход набор задач,
веса этих задач и параметры оптимизации.

**Примечание:** для указания количества запусков при оценке качества *эскиза*
на вход `ms.tune.tune_tasks` передается объект ```ms.runner.LocalRunner```
с указанием параметра ```ms.runner.config.EvaluatorConfig```. 

In [ ]:
def tune_ms(
    tasks: list[tvm.meta_schedule.tune_context.TuneContext, ...], 
    task_weights: list[int, ...], 
    work_dir: str, 
    n_trials: int
):
    """
    Параметры:
        tasks: Список задач.
        task_weights: Список весов задач.
        work_dir: Директория для логирования результатов оптимизации.
        n_trial: Количество экспериментов для каждой задачи.
    """
    
    # <ОПТИМИЗАЦИЯ ПОДГРАФОВ С ПОМОЩЬЮ METASCHEDULER>


Далее выполним запуск оптимизации с помощью MetaScheduler посредством вызова
функции ```tune_ms```, установив число экспериментов при оптимизации равным
```N * len(tasks)```.

In [ ]:
n_trial_per_task = global_trial

if is_x86():
    tune_ms(tasks, task_weights, work_dir, n_trial_per_task * len(tasks))

После оптимизации можно скомпилировать нейронную с учетом построенных оптимизаций
с помощью интерфейса MetaScheduler ```ms.relay_integration.compile_relay```.

In [ ]:
if is_x86():
    
    database = ms.database.JSONDatabase(
        f"{work_dir}/database_workload.json",
        f"{work_dir}/database_tuning_record.json",
        allow_missing=False
    )

    lib = ms.relay_integration.compile_relay(
        database, mod, target, params,
        opt_level=opt_level,
    )

В завершении измерим время вывода с использованием функции `timeit_inference`,
определим качество работы модели с помощью функции `get_accuracy` и выполним
проверку корректности работы оптимизированной модели, сравнив полученное значение
показателя точности с референсным.

In [ ]:
if is_x86():
    
    ms_logreg_predict, ms_logreg_times = timeit_inference(mod, lib, images)

    ms_logreg_accuracy = get_accuracy(labels, ms_logreg_predict)
    assert np.allclose(metric['logreg'], ms_logreg_accuracy, rtol=1e-5)

    ms_logreg_time = np.median(ms_logreg_times)
    print(f'Медианное время работы после оптимизации слоев с помощью MetaScheduler: {ms_logreg_time:.4f} мc')

### 6.5. Анализ полученных результатов

Для анализа результатов оптимизации нейронной сети с использованием различных методов
построим прафик медианного времени выполнения.

In [ ]:
fig, ax = plt.subplots()

name = ['Без оптимизации\nслоев', 'AutoTVM', 'Auto-scheduler', 'MetaScheduler']
times = [default_logreg_time, autotvm_logreg_time, autoscheduler_logreg_time, ms_logreg_time]
bar_labels = ['red', 'blue', '_red', 'orange']
bar_colors = ['tab:blue', 'tab:red', 'tab:green', 'tab:orange']

bars = ax.bar(name, times, label=name, color=bar_colors)
ax.set_title('Среднее время\nвыполнения (мс)', fontsize=18)

for bar, n, t in zip(bars, name, times):
    h = bar.get_height()
    if n == 'Без оптимизации\nслоев': h = h / 2
    if h != 0:
        ax.text(
            bar.get_x() + bar.get_width() / 2,
            h,
            f'{round(t, 4)} с',
            ha='center',
            va='bottom',
            fontsize=15,
        )

ax.xaxis.label.set_size(40)
ax.set_title('Среднее время\nвыполнения (с)', fontsize=18)
plt.grid()

 **Вывод:** <НАПИСАТЬ ВЫВОДЫ ПО РЕЗУЛЬТАТАМ ОПТИМИЗАЦИИ ЛОГИСТИЧЕСКОЙ РЕГРЕССИИ>

## 7. Запуск и оптимизация полносвязной нейронной сети

### 7.1. Компиляция и запуск модели

Вначале необходимо выполнить загрузку модели полносвязной нейронной сети.
Следует учитывать что в данной модели больше слоев и, следовательно, будут 
другие промежуточные и финальные результаты работы методов, например, количество
и веса извлеченных задач, результаты оптимизации.

In [ ]:
default_fcnn_time, autotvm_fcnn_time, ms_fcnn_time = 0, 0, 0

mod, params = load_model('model/fcnn.json', 'model/fcnn.params')
print(mod['main'])

Следующий шаг - компиляция модели без оптимизации слоев.

In [ ]:
with tvm.transform.PassContext(opt_level=opt_level):
    lib = relay.build(mod, target=target, params=params)

После компиляции можно выполнить запуск вывода и измерение времени выполнения с использованием
разработанной функции `timeit_inference`, а также проверку качества работы полносвязной нейронной сети
после загрузки с помощью функции `get_accuracy` и сравнение полученной точности классификации
с загруженным значением, которое получено на x86-64.

In [ ]:
default_fcnn_predict, default_fcnn_times = timeit_inference(mod, lib, images)

default_fcnn_accuracy = get_accuracy(labels, default_fcnn_predict)
assert np.allclose(metric['fcnn'], default_fcnn_accuracy, rtol=1e-5)

default_fcnn_time = np.median(default_fcnn_times)
print(f'Медианное время работы не оптимизированной модели: {default_fcnn_time:.4f} мc')

### 7.2. Использование возможностей AutoTVM

Вызовем разработанную функцию ```get_autotvm_task``` для извлечения задач
из графа вычислений для AutoTVM.

In [ ]:
tasks = get_autotvm_task(mod, target, params)

Для запуска оптимизации с помощью AutoTVM необходимо определить файл ```log_file```
для логирования результатов оптимизации, установить число экспериментов при оптимизации,
а затем вызвать разработанную функцию ```tune_autotvm```.

In [ ]:
log_file = 'autotvm/autotvm_fcnn.log'
n_trial = global_trial

tune_autotvm(tasks, n_trial, log_file)

Перед использованием оптимизированной модели, необходимо выполнить компиляцию модели
с учетом истории оптимизации, которая была сохранена в файл `log_file`.

In [ ]:
with autotvm.apply_history_best(log_file):
    with tvm.transform.PassContext(opt_level=opt_level):
        lib = relay.build(mod, target=target, params=params)

На данном этапе можно выполнить измерение времени выполнения с использованием функции
`timeit_inference`, проверку качества работы оптимизированной модели с помощью функции
`get_accuracy` и сравнение точности классификации с рефенсным значением, которое было
получено после запуска обучения модели.

In [ ]:
autotvm_fcnn_predict, autotvm_fcnn_times = timeit_inference(mod, lib, images)

autotvm_fcnn_accuracy = get_accuracy(labels, autotvm_fcnn_predict)
assert np.allclose(metric['fcnn'], autotvm_fcnn_accuracy, rtol=1e-5)

autotvm_fcnn_time = np.median(autotvm_fcnn_times)
print(f'Медианное время работы после оптимизации слоев с помощью AutoTVM: {autotvm_fcnn_time:.4f} мc')

### 7.3. Применение MetaScheduler

Вызовем разработанную функцию ```get_ms_task```, предварительно определив
директорию ```work_dir``` для логирования результатов оптимизации.

В данном случае строка компиляции уже содержит информацию о числе потоков,
поэтому модифицировать ее нет необходимости.

In [ ]:
if is_x86():
    work_dir = "meta_schedule_fcnn"

    tasks, task_weights = get_ms_task(mod, target, params, opt_level, work_dir)

Далее выполним запуск оптимизации с помощью MetaScheduler посредством вызова
функции ```tune_ms```, установив число экспериментов при оптимизации равным
```N * len(tasks)```.

In [ ]:
n_trial_per_task = global_trial

if is_x86():
    tune_ms(tasks, task_weights, work_dir, n_trial_per_task * len(tasks))

После оптимизации можно скомпилировать нейронную с учетом построенных оптимизаций
с помощью интерфейса MetaScheduler ```ms.relay_integration.compile_relay```.

In [ ]:
if is_x86():
    
    database = ms.database.JSONDatabase(
        f"{work_dir}/database_workload.json",
        f"{work_dir}/database_tuning_record.json",
        allow_missing=False
    )

    lib = ms.relay_integration.compile_relay(
        database, mod, target, params,
        opt_level=opt_level,
    )

В завершении измерим время вывода с использованием функции `timeit_inference`,
определим качество работы модели с помощью функции `get_accuracy` и выполним
проверку корректности работы оптимизированной модели, сравнив полученное значение
показателя точности с референсным.

In [ ]:
if is_x86():
    ms_fcnn_predict, ms_fcnn_times = timeit_inference(mod, lib, images)

    ms_fcnn_accuracy = get_accuracy(labels, ms_fcnn_predict)
    assert np.allclose(metric['fcnn'], ms_fcnn_accuracy, rtol=1e-5)

    ms_fcnn_time = np.median(ms_fcnn_times)
    print(f'Медианное время работы после оптимизации слоев с помощью MetaScheduler: {ms_fcnn_time:.4f} мc')

### 7.4. Анализ результатов

Для анализа результатов оптимизации нейронной сети с использованием различных методов
построим прафик медианного времени выполнения.

In [ ]:
fig, ax = plt.subplots()

name = ['Без оптимизации\nслоев', 'AutoTVM', 'MetaScheduler']
times = [default_fcnn_time, autotvm_fcnn_time, ms_fcnn_time]

bars = ax.bar(name, times, label=name, color=bar_colors)
ax.set_title('Среднее время\nвыполнения (мс)', fontsize=18)

for bar, n, t in zip(bars, name, times):
    h = bar.get_height()
    if n == 'Без оптимизации\nслоев': h = h / 2
    if h != 0:
        ax.text(
            bar.get_x() + bar.get_width() / 2,
            h,
            f'{round(t, 4)} с',
            ha='center',
            va='bottom',
            fontsize=15,
        )

ax.xaxis.label.set_size(40)
ax.set_title('Среднее время\nвыполнения (с)', fontsize=18)
plt.grid()

**Вывод:** <НАПИСАТЬ ВЫВОДЫ ИЗ РЕЗУЛЬТАТОВ ОПТИМИЗАЦИИ ПОЛНОСВЯЗНОЙ СЕТИ>